### **MÉTRICAS DE RELEVANCIA PARA POSTERIORES ANÁLISIS**

In [1]:
import pandas as pd

df = pd.read_csv("data/processed/rome_clean.csv")

------------------------------------------------------------------------------------------------------------------------------------------------

**Precio por Minuto**

In [2]:
df["price_per_min"] = df["price"] / (df["tt"] / 60)
df["price_per_min"]

0        0.280152
1        0.380769
2        0.272699
3        6.150000
4        0.200000
           ...   
24174    0.292518
24175    0.364286
24176    0.280719
24177    0.552685
24178    0.225949
Name: price_per_min, Length: 24179, dtype: float64

En un sistema real de patinetes eléctricos, el precio por minuto debe ser prácticamente constante. Haciendo una breve visualización, ya vemos como este valor no lo es. Aunque en la mayoría de casos tiene valores muy similares, en otros casos, este recoge valores atípicos.

In [3]:
df["price_per_min"].describe()

count    24179.000000
mean         0.375179
std          0.451250
min          0.158333
25%          0.220588
50%          0.275261
75%          0.380769
max          7.650000
Name: price_per_min, dtype: float64

Tanto la desviación estándar, cómo el valor máximo son valores demasiado grandes. Un sistema de patinetes suele tener tarifas entre 0.15 - 0.30 euros el minuto. Por lo que un std típico rondaría los 0.01 - 0.03. Por tanto deben haber outliers bastante fuertes. Hasta ahora, una breve conclusión que podemos sacar, es que la tarifa real está entre 0.22 y 0.40 €/min.

In [4]:
(df["price_per_min"] > 1).sum()

np.int64(770)

In [5]:
df[df["price_per_min"] > 1]

idS                  tsO                  tsD   price  tt         dis  \
3      A0H4  2021-02-14 14:35:03  2021-02-14 14:35:13  1.0250  10    3.712940   
55     A0N7  2021-02-05 17:54:33  2021-02-05 17:55:04  1.0775  31   46.656129   
63     A0N7  2021-02-16 16:00:04  2021-02-16 16:01:04  1.1500  60  258.123807   
121    A0U7  2021-02-19 12:12:14  2021-02-19 12:13:13  1.1475  59  153.820969   
137    A1E3  2021-02-24 13:30:43  2021-02-24 13:31:34  1.1275  51  197.166231   
...     ...                  ...                  ...     ...  ..         ...   
24066  Z9D4  2021-02-08 14:03:54  2021-02-08 14:04:53  1.1475  59   88.668503   
24067  Z9D4  2021-02-09 14:05:33  2021-02-09 14:05:43  1.0250  10   20.747120   
24102  Z9N9  2021-02-18 12:58:13  2021-02-18 12:59:13  1.1500  60  100.907723   
24106  Z9N9  2021-02-19 17:27:53  2021-02-19 17:28:53  1.1500  60   84.208273   
24110  Z9N9  2021-02-25 17:23:43  2021-02-25 17:23:54  1.0275  11   30.892273   

             vel       lonO       latO       lonD       latD  duration_calc  \
3       1.336658  12.486283  41.928267  12.486276  41.928300           10.0   
55      5.418131  12.533272  41.877671  12.532951  41.878013           31.0   
63     15.487428  12.459043  41.871970  12.456557  41.872047           60.0   
121     9.385686  12.482335  41.882810  12.480872  41.883489           59.0   
137    13.917616  12.466351  41.911304  12.467459  41.910108           51.0   
...          ...        ...        ...        ...        ...            ...   
24066   5.410282  12.474311  41.889916  12.474844  41.890283           59.0   
24067   7.468963  12.474836  41.890240  12.474586  41.890250           10.0   
24102   6.054463  12.446295  41.874928  12.447173  41.875542           60.0   
24106   5.052496  12.494108  41.896339  12.493598  41.895701           60.0   
24110  10.110198  12.473708  41.876617  12.473491  41.876843           11.0   

       price_per_min  
3           6.150000  
55          2.085484  
63          1.150000  
121         1.166949  
137         1.326471  
...              ...  
24066       1.166949  
24067       6.150000  
24102       1.150000  
24106       1.150000  
24110       5.604545  

[770 rows x 13 columns]

Como podemos observar, los valores que tienen un precio por minuto más elevado, son aquellos cuyos tiempos son inferiores a 1 minuto. Esto problemente ocurra, ya que seguramente haya un precio de desanclaje que no viene recogido ni especificado. Confirmemos nuestra teoría.

In [6]:
((df["price_per_min"] > 1) & (df["tt"] < 60)).sum()

np.int64(537)

Efectivamente de los casi 800 casos de precio por minuto mayor a 1,  537 se deben a que el tiempo de uso fue inferior a 1 minuto. Podríamos seguir haciendo pruebas, pero esto ya nos da una orientación de que cuanto más corto es el viaje, menos ecónomico te sale respecto al tiempo de uso.

NOTA: que salga el precio al minuto por ejemplo 6, no quiere decir que hayan pagado eso.

Una vez llegado a esta conclusión:

`price = unlock_fee + (price_per_min × minutes)`

Por tanto, podemos estimar automáticamente el precio fijo de desanclaje usando **regresión lineal** simple.

y = a + bx

- y = precio total

- x = minutos del viaje

- a = precio de desanclaje

- b = precio por minuto

In [7]:
from sklearn.linear_model import LinearRegression

df_clean = df[(df["tt"] > 0) & (df["price"] > 0)]

X = (df_clean["tt"] / 60).values.reshape(-1, 1)
y = df_clean["price"].values

model = LinearRegression().fit(X, y)

unlock_fee = model.intercept_
price_per_min = model.coef_[0]

print(f"Precio de desanclaje: {unlock_fee} €")
print(f"Precio por minuto: {price_per_min} €")

Precio de desanclaje: 1.0000000000000033 €
Precio por minuto: 0.1499999999999997 €


In [8]:
import plotly.express as px

df_clean = df[(df["tt"] > 0) & (df["price"] > 0)]
df_clean["minutes"] = df_clean["tt"] / 60

df_clean["expected_price"] = unlock_fee + price_per_min * df_clean["minutes"]
df_clean["unlock_fee_line"] = unlock_fee
df_clean["variable_component"] = price_per_min * df_clean["minutes"]

fig = px.scatter(df_clean, x="minutes", y="price", opacity=0.6)

fig.add_scatter(x=df_clean["minutes"], y=df_clean["expected_price"], mode="lines", name="Precio estimado")
fig.add_scatter(x=df_clean["minutes"], y=df_clean["unlock_fee_line"], mode="lines", name="Precio fijo (1 €)")
fig.add_scatter(x=df_clean["minutes"], y=df_clean["variable_component"], mode="lines", name="Componente variable")

fig.update_layout(title="Desglose del precio: fijo + por minuto",
                  xaxis_title="Tiempo (Minutos)",
                  yaxis_title="Precio (€)")

fig.show()

## **Precio fijo: 1 €**
## **Precio variable por minuto: 0.15 €**

---------------------------------------------------------------------------------------------------------------------------------------------

### OTRAS MÉTRICAS (a realizar)

1. Económicas

Precio por minuto

Precio por kilómetro

Price elasticity (si quieres subir nivel)

2. Espaciales

Distancia línea recta vs distancia real

Índice de rectitud (“tortuosity”)

Distribución de distancias por viaje

3. Temporales

Demanda por hora del día

Demanda por día de la semana

Duración media según franja horaria

Velocidad media por hora

4. Operativas

Viajes por patinete

Tiempo muerto entre viajes (idle time)

Porcentaje de patinetes que trabajan más/menos